In [1]:
import requests

options = {"symbol": "eth", "count":144, "interval":"10m"}

def fetchPrice(options = options):
    url =f"https://satoshi.opera-api.com/v1/exchangerates/historical/{options['symbol']}?count={options['count']}&interval={options['interval']}"
    print(url)
    return requests.get(url).json()
#fetchPrice()

In [2]:
import numpy as np
import pandas as pd

def priceDf(options = options):
    data = fetchPrice(options)["data"]
    np_price = np.ndarray((len(data),2))
    for i, x in enumerate(data):
        np_price[i,1] = x["price"]
        np_price[i,0] = x["time"]/(60*1000)
    return np_price

#priceDf()

In [3]:
import plotly.graph_objects as go
from lltb import largest_triangle_three_buckets as lltb

def plotList(df):
    fig = go.Figure([go.Scatter(x=pd.to_datetime(df[:,0], unit="m"), y=df[:,1],
                            marker_color='black',
                            opacity=0.6,
                            name="")])
    
    fig.show()
    

def plotPrice(options = options, sample = None):
    data = priceDf(options)
    if sample:
        data_ = lltb(data.tolist(), int(len(data)*sample))
        print(f"Downsampling data from {len(data)} to {len(data_)} data points")
        data = data_
    print(f"Plotting {len(data)} data points")
    plotList(np.array(data))

#plotPrice(options,0.5)


In [4]:
def monthsToMin(months):
    return months*30*24*60

def resolution(minutes, months):
    return int(monthsToMin(months)/minutes)

resolution(180,1)

def optionsFrom(symbol, interval, months):
    options = {"symbol": symbol, "count": resolution(interval, months), "interval": f"{interval}m"}
    if(interval > 60): options["interval"] = f"{int(interval/60)}h"
    return options

#optionsFrom("eth", 240, 1)

In [5]:
plotPrice(optionsFrom("eth", 120, 1))

https://satoshi.opera-api.com/v1/exchangerates/historical/eth?count=360&interval=2h
Plotting 360 data points


In [6]:
# Downsampled using [Largest triangle three buckets](https://skemman.is/bitstream/1946/15343/3/SS_MSthesis.pdf)
plotPrice(optionsFrom("eth", 1, 1),1/98)

https://satoshi.opera-api.com/v1/exchangerates/historical/eth?count=43200&interval=1m
Downsampling data from 35253 to 359 data points
Plotting 359 data points


In [7]:
plotPrice(optionsFrom("eth", 1, 1))

https://satoshi.opera-api.com/v1/exchangerates/historical/eth?count=43200&interval=1m
Plotting 35254 data points
